In [2]:
!pip install ydata-profiling

  Using cached numpy-1.25.2-cp311-cp311-macosx_11_0_arm64.whl.metadata (5.6 kB)
Using cached numpy-1.25.2-cp311-cp311-macosx_11_0_arm64.whl (14.0 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 1.26.4
    Uninstalling numpy-1.26.4:
      Successfully uninstalled numpy-1.26.4


In [1]:
'''EDA = Exploratory Data Analysis'''
import io

import pandas as pd
from dotenv import load_dotenv, find_dotenv
from ydata_profiling import ProfileReport

from pfeed.const.paths import DATA_PATH
from pfeed import bybit
from pfeed.sources.bybit.const import DATA_SOURCE

%load_ext autoreload
# Reload all modules (except those excluded by %aimport) every time before executing the Python code typed.
%autoreload 2

load_dotenv(find_dotenv())

Using MinIO as datastore


True

In [2]:
pdt = 'BTC_USDT_PERP'
date = '2023-11-09'

Load raw data

In [3]:
data = bybit.extract_data(pdt, date, 'raw')
raw_df = pd.read_csv(io.BytesIO(data), compression='gzip')

print(f'{raw_df.shape=}')
raw_df.head()

raw_df.shape=(2262675, 10)


timestamp   symbol  side   size    price  tickDirection  \
0  1.699488e+09  BTCUSDT  Sell  0.418  35641.6      MinusTick   
1  1.699488e+09  BTCUSDT  Sell  0.300  35641.6  ZeroMinusTick   
2  1.699488e+09  BTCUSDT  Sell  1.879  35641.6  ZeroMinusTick   
3  1.699488e+09  BTCUSDT  Sell  0.090  35641.6  ZeroMinusTick   
4  1.699488e+09  BTCUSDT  Sell  0.130  35641.6  ZeroMinusTick   

                             trdMatchID    grossValue  homeNotional  \
0  ab99ce71-648e-58ab-a79a-5bc9c5e9e4f8  1.489819e+12         0.418   
1  93007a7a-8fd1-5729-a0d5-f3e375301b64  1.069248e+12         0.300   
2  a6301d83-df8a-5d0c-ac82-fe3480a9b411  6.697057e+12         1.879   
3  0c079b43-4f35-5f6b-b153-36d27405b572  3.207744e+11         0.090   
4  758b503e-5c73-56b2-8561-b4977e8291f6  4.633408e+11         0.130   

   foreignNotional  
0       14898.1888  
1       10692.4800  
2       66970.5664  
3        3207.7440  
4        4633.4080

In [6]:
ProfileReport(raw_df, title=f'{DATA_SOURCE} Raw Data Profiling Report')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Load tick data

In [33]:
data = bybit.extract_data(pdt, date, 'tick')
tick_df = pd.read_parquet(io.BytesIO(data))
tick_df.set_index('ts', inplace=True)
tick_df.index = pd.to_datetime(tick_df.index, unit='s')
tick_df.head()

side  quantity    price
ts                                                    
2023-11-09 00:00:00.133199872    -1     0.418  35641.6
2023-11-09 00:00:00.184999936    -1     0.300  35641.6
2023-11-09 00:00:00.202300160    -1     1.879  35641.6
2023-11-09 00:00:00.202300160    -1     0.090  35641.6
2023-11-09 00:00:00.202300160    -1     0.130  35641.6

Load second/minute/hour/daily data

In [13]:
data_type = 'second'  # second/minute/hour/daily
data = bybit.extract_data(pdt, date, data_type)
df = pd.read_parquet(io.BytesIO(data))
df.head()

num_buys  num_sells  quantity  buy_quantity  \
ts                                                                 
2023-11-09 00:00:00        11         22    10.976         3.144   
2023-11-09 00:00:01       103          5    57.193        56.400   
2023-11-09 00:00:02        10          8     5.544         4.478   
2023-11-09 00:00:03         4         12     0.740         0.224   
2023-11-09 00:00:04        25          8    23.985        22.889   

                     sell_quantity     open     high      low    close first  
ts                                                                            
2023-11-09 00:00:00          7.832  35641.6  35641.7  35636.2  35636.4     H  
2023-11-09 00:00:01          0.793  35636.4  35652.4  35636.3  35652.4     L  
2023-11-09 00:00:02          1.066  35649.2  35649.9  35649.2  35649.2     L  
2023-11-09 00:00:03          0.516  35649.3  35649.3  35641.5  35641.5     H  
2023-11-09 00:00:04          1.096  35641.5  35647.7  35641.5  35644.2     L